### 2023 ARIS Ingest Code and Data Checking 
January 20, 2023; UPDATED: January 22, 2023 MJW
Added file seletion GUI.
- Accession
- Title
- Objectives
- Approach

#### Step 1. Check for duplicate accessions within each ARS input file type (Projects, Objectives, Approach) across HQ input files (see ARISdupecheck.ipynb).
#### Step 2. Make sure that every cell with text in the Excel files ends with a period, followed by a space (CRITICAL).
#### Step 3. Open each ARS input csv and create a data frame, and append them together into one data frame.
#### Step 4. Generate final output of selected text for accession, title, abstract (objective+approach) as cogx files.
#### Step 6. Compress files into a zip folder for upload into a Cogito Studio Express project (see step-by-step instructions).

In [1]:
# %run -i guifunc.py
import guifunc
# from guifunc import selectfiles
labelfnames = guifunc.selectFiles()

labelfnames {'workingdir': 'C:\\Users\\jennifer.woodward\\ARISdata\\ARISdata_2023_Jan_23'}
3 files selected
 ('D:/ExHD-github/IIB-RnD/ARIS/Data/excel-input-files/FY22-Q3/A416_Approach_07_05_2022.xlsx', 'D:/ExHD-github/IIB-RnD/ARIS/Data/excel-input-files/FY22-Q3/A416_Objective_07_05_2022.xlsx', 'D:/ExHD-github/IIB-RnD/ARIS/Data/excel-input-files/FY22-Q3/A416_Projects_07_05_2022.xlsx')

Input files:
projects_infile = D:/ExHD-github/IIB-RnD/ARIS/Data/excel-input-files/FY22-Q3/A416_Projects_07_05_2022.xlsx
objective_infile = D:/ExHD-github/IIB-RnD/ARIS/Data/excel-input-files/FY22-Q3/A416_Objective_07_05_2022.xlsx
approach_infile = D:/ExHD-github/IIB-RnD/ARIS/Data/excel-input-files/FY22-Q3/A416_Approach_07_05_2022.xlsx

ARIS csv files unit tested for csv format.
 Prepped csv files saved for processing in C:\Users\jennifer.woodward\ARISdata\ARISdata_2023_Jan_23

Prepped for processing as csv:
projects_file = C:\Users\jennifer.woodward\ARISdata\ARISdata_2023_Jan_23\A416_Projects_07_05_2022.cs

### Run the next code cell to see the File Selection GUI. 
### Select THREE files at once:
#### ARIS 'Projects', 'Objective', and 'Approach' .xlsx files (hold the CNTRL or SHIFT key to select multipe files).

In [2]:
print(labelfnames)
print('\n', labelfnames.keys())

{'workingdir': 'C:\\Users\\jennifer.woodward\\ARISdata\\ARISdata_2023_Jan_23', 'approach': 'D:/ExHD-github/IIB-RnD/ARIS/Data/excel-input-files/FY22-Q3/A416_Approach_07_05_2022.xlsx', 'objective': 'D:/ExHD-github/IIB-RnD/ARIS/Data/excel-input-files/FY22-Q3/A416_Objective_07_05_2022.xlsx', 'projects': 'D:/ExHD-github/IIB-RnD/ARIS/Data/excel-input-files/FY22-Q3/A416_Projects_07_05_2022.xlsx', 'approachcsv': 'C:\\Users\\jennifer.woodward\\ARISdata\\ARISdata_2023_Jan_23\\A416_Approach_07_05_2022.csv', 'objectivecsv': 'C:\\Users\\jennifer.woodward\\ARISdata\\ARISdata_2023_Jan_23\\A416_Objective_07_05_2022.csv', 'projectscsv': 'C:\\Users\\jennifer.woodward\\ARISdata\\ARISdata_2023_Jan_23\\A416_Projects_07_05_2022.csv'}

 dict_keys(['workingdir', 'approach', 'objective', 'projects', 'approachcsv', 'objectivecsv', 'projectscsv'])


In [3]:
# Imports
import pandas as pd
import os
import glob
import numpy as np
import functools as ft
import sys

In [4]:
# Input ARIS files (csv).
# projects_file = 'D:\\ExHD-github\\IIB-RnD\\ARIS\\Data\\excel-input-files\\CSV\\A416_Projects_01_03_2023.csv'
# objectives_file = 'D:\\ExHD-github/IIB-RnD\\ARIS\\Data\\excel-input-files\\CSV\\A416_Objective_01_03_2023.csv'
# approach_file = 'D:\\ExHD-github\\IIB-RnD\\ARIS\\Data\\excel-input-files\\CSV\\A416_Approach_01_03_2023.csv'

projects_file = labelfnames['projectscsv']
objectives_file = labelfnames['objectivecsv']
approach_file = labelfnames['approachcsv']
workingcvs_dir = labelfnames['workingdir']

# Identify and change to the input ARIS files directory so new files will be saved with the input files.
# cwd, _ = os.path.split(projects_file)
# os.chdir(cwd)
# print('Working in directory', cwd)

# Instantiate input files list for processing.
arisinputs = [projects_file, objectives_file, approach_file]
print('arisinputs for analysis\n', arisinputs)

arisinputs for analysis
 ['C:\\Users\\jennifer.woodward\\ARISdata\\ARISdata_2023_Jan_23\\A416_Projects_07_05_2022.csv', 'C:\\Users\\jennifer.woodward\\ARISdata\\ARISdata_2023_Jan_23\\A416_Objective_07_05_2022.csv', 'C:\\Users\\jennifer.woodward\\ARISdata\\ARISdata_2023_Jan_23\\A416_Approach_07_05_2022.csv']


In [5]:
# Check ARS Project (Titles), Objectives, and Approach input files provided for Qa and Qb. Open each as a list, combine
# to one list, and check for count (rows - 1 for the header row) duplicates accession numbers in each (DATA CHECK). 
# If duplicates, take action. The 6 numbers print out below in DATA CHECK should all be the same.

print('DATA CHECK: Projects (Titles):') 
with open(projects_file, 'r', encoding='utf-8', errors='ignore') as f:
    dataP = f.readlines()
print(type(dataP), 'accessions:', len(dataP)-1, ', accessions less duplicates:',  len(set(dataP))-1,'\n')

print('DATA CHECK: Objective:')
with open(objectives_file, 'r', encoding='utf-8', errors='ignore') as f:
    dataO = f.readlines()
print(type(dataO), 'accessions:', len(dataO)-1, ', accessions less duplicates:',  len(set(dataO))-1, '\n')

print('DATA CHECK: Approach:')
with open(approach_file, 'r', encoding='utf-8', errors='ignore') as f:
    dataA = f.readlines()
print(type(dataA), 'accessions:', len(dataA)-1, ', accessions less duplicates:', len(set(dataA))-1)

DATA CHECK: Projects (Titles):
<class 'list'> accessions: 166 , accessions less duplicates: 166 

DATA CHECK: Objective:
<class 'list'> accessions: 179 , accessions less duplicates: 179 

DATA CHECK: Approach:
<class 'list'> accessions: 166 , accessions less duplicates: 166


In [6]:
# Open each ARS input csv file and convert to a data frame, add each data frame object to a list of data frames, and
# check how many projects are listed in each for Qa and Qb title, objectives, approach. Sometimes the column A header 
# (Accession) has encoding issues which interfere with processing. This is check and if needed, corrected here. 

dfs = []

print('Data check')
for fname in arisinputs:

    newdf = pd.read_csv(fname, encoding='ISO-8859-1')
    newdf.columns = [c.replace(' ', '_') for c in newdf.columns]
    print('\n', fname)
    print(type(newdf), len(newdf))
    
    print('original keys', newdf.keys())
    
    # Accession was giving unicode error - a fix.
    for key in newdf.keys():
#         print(key)
        keycheck = len(str(key))
#         print('keycheck', keycheck)
        if 'Accession' in key:
            if len('Accession') != keycheck:
                newdf['Accession'] = newdf.pop(key)

    dfs.append(newdf)
    print('updated keys', newdf.keys())
    print('===')            

Data check

 C:\Users\jennifer.woodward\ARISdata\ARISdata_2023_Jan_23\A416_Projects_07_05_2022.csv
<class 'pandas.core.frame.DataFrame'> 166
original keys Index(['Accession', 'Project_Number', 'Project_Title'], dtype='object')
updated keys Index(['Accession', 'Project_Number', 'Project_Title'], dtype='object')
===

 C:\Users\jennifer.woodward\ARISdata\ARISdata_2023_Jan_23\A416_Objective_07_05_2022.csv
<class 'pandas.core.frame.DataFrame'> 166
original keys Index(['Accession', 'Objective'], dtype='object')
updated keys Index(['Accession', 'Objective'], dtype='object')
===

 C:\Users\jennifer.woodward\ARISdata\ARISdata_2023_Jan_23\A416_Approach_07_05_2022.csv
<class 'pandas.core.frame.DataFrame'> 166
original keys Index(['Accession', 'Approach'], dtype='object')
updated keys Index(['Accession', 'Approach'], dtype='object')
===


In [7]:
# Full analyses of each field accession, project number, title, objectives, approach for differences from Qa to Qb.
# Merge the data frames (ft.reduce), how = outer to grab all accessions in Qa and Qb.
# Create column for boolean values for 'True' if Qa = Qb, or 'False' if Qa does not = Qb for each of these fields.
# DATA CHECK: Print out values for columns generated by Pandas in appending these files, and the added columns so far. 

# Combine the three input dataframes, rename Title, and set the Accession numbers as the index
result = ft.reduce(lambda left, right: pd.merge(left, right, on='Accession', how='outer'), dfs)
result = result.set_index('Accession')
result['Title'] = result['Project_Title']

# Combine the Objective, Approach, with a required space between them into one column, called 'Abstract'.
result['Abstract'] = result["Objective"].str.cat(result["Approach"], sep = " ")

# Drop uneccessary columns
result = result.drop(['Project_Number'], axis=1)
result = result.drop(['Project_Title'], axis=1)
result = result.drop(['Objective'], axis=1)
result = result.drop(['Approach'], axis=1)

In [8]:
# Display FULL SUMMARY findings, each quarter data, decisions, and selected text to annotate in the 'result' data frame.
# Pandas df settings to show all data in the jupyter notebook for easier review and data checking.
pd.set_option('display.max_columns', None)
pd.set_option('display.max_colwidth', None)  # or 199
pd.set_option('display.max_rows', None)
pd.set_option('display.width', 1000)
pd.set_option('display.colheader_justify', 'center')
pd.set_option('display.precision', 3)

# result = result.set_index('Accession')
print('\nDATA CHECK:')
print('CONDUCT ACTIVE REVIEW at:\n\t', os.path.sep.join([workingcvs_dir,'out','ARIS_accn_title_abstract_input.csv.']))
display(result)
print('CONDUCT ACTIVE REVIEW at:\n\t', os.path.sep.join([workingcvs_dir, 'out','ARIS_accn_title_abstract_input.csv.']))

# Save for easier review before making cogx files if needed; look for periods, spaces. Update ARIS input files if needed.
try:
    os.mkdir(os.path.sep.join([workingcvs_dir, 'out']))
except FileExistsError:
    pass

result.to_csv(os.path.sep.join([workingcvs_dir,'out','ARIS_accn_title_abstract_input.csv']))


DATA CHECK:
CONDUCT ACTIVE REVIEW at:
	 C:\Users\jennifer.woodward\ARISdata\ARISdata_2023_Jan_23\out\ARIS_accn_title_abstract_input.csv.


Title                                                                                                    \
Accession                                                                                                                                                                                                             
438987                                                                                                                        Improving Sustainability of Dairy and Forage Production Systems for the Upper Midwest   
439564                                                                                                Incidence of Bacterial Pathogens in Regulated Foods and Applied Processing Technologies for Their Destruction   
439671                                                                                                    Genomic and Epidemiological Parameters to Inform Interventions Strategies for Enteric Diseases of Poultry   
440376                                                                                                                           Advanced Methods for Predictive Modeling of Bacterial Growth and Survival in Foods   
440440                                                                                                   Integrative Genomic and Biological Approaches to Detect and Manage Emerging Foreign Fungal Plant Pathogens   
440524                                                                                                                      Improved Management, Quality and Utilization of Alfalfa for Dairies in the Western U.S.   
440529                                                                                                                          Detection, Quantification and Characterization Technologies for Foodborne Pathogens   
440677                                                                                                                   Elucidating the Pathobiology and Transmission of Transmissible Spongiform Encephalopathies   
440718                                                                                 Innovative Manure Treatment Technologies and Enhanced Soil Health for Agricultural Systems of the Southeastern Coastal Plain   
440790                                                                                                                                Advancement of Sensing Technologies for Food Safety and Security Applications   
440891                                                                   Soil, Crop, and Manure Biochemistry and Molecular Ecology: Bridging Knowledge Gaps in Microbiome Response to Management and Climate Change   
440922                                                                                          Sustainable Management of Manure Nutrients and Environmental Contaminants from Beef and Swine Production Facilities   
440930                                                                                                                 Holistic Tactics to Advance the Microbiological Safety and Quality of the Red Meat Continuum   
440948       Analysis of Genetic Factors that Increase Foodborne Pathogen Fitness, Virulence, and Antimicrobial Resistance Transfer, to Identify Interventions against Salmonella and Campylobacter in Food Animals   
440963                                                                                                                                      Exploration for Natural Enemies in China for Citrus psyllid in the U.S.   
440973     Improving Pre-harvest Produce Safety through Reduction of Pathogen Levels in Agricultural Environments and Development and Validation of Farm-Scale Microbial Quality Model for Irrigation Water Sources   
441096                                                          Developing Agronomically and Environmentally Beneficial Management Practices to Increase the Sustainability and Safety of Animal Manure Utilization   
441097                 

CONDUCT ACTIVE REVIEW at:
	 C:\Users\jennifer.woodward\ARISdata\ARISdata_2023_Jan_23\out\ARIS_accn_title_abstract_input.csv.


### Cell output cleared for space; run code to view.

In [9]:
# DATA CHECK for period, space at the end of each field.
# String to be searched in end of string 
search ="."
  
# boolean series returned with False at place of NaN
result['title_pd_space'] = result['Title'].str.endswith(search)
result['abstract_pd_space'] = result['Abstract'].str.endswith(search)
  
# display boolean series results
print('DATA CHECK Formatting for Cogito:')
# if False in result['title_pd_space']:
#     print("One or more titles does not have a period, space at the end; update the csv input files and rerun code.")
# else:
#     print('All titles are formatted with a period, space at the end; all set to make cogx files.')
    
# if False in result['abstract_pd_space']:
#     print("One or more abstracts does not have a period, space at the end; update the csv input files and rerun code.")
# else:
#     print('All abstracts are formatted with a period, space at the end; all set to make cogx files.')
print('\n>>>>>>>>>>Does the Title field end in a period?')
display(result['title_pd_space'])
print('>>>>>>>>>>Does the Abstract field end in a period?')
display(result['abstract_pd_space'])
display(result)

DATA CHECK Formatting for Cogito:

>>>>>>>>>>Does the Title field end in a period?


Accession
438987    False
439564    False
439671    False
440376    False
440440    False
440524     True
440529    False
440677    False
440718    False
440790    False
440891    False
440922    False
440930    False
440948    False
440963     True
440973    False
441096    False
441097    False
441098    False
441102    False
441106    False
441109    False
441117    False
441119    False
441124    False
441129    False
441143    False
441144    False
441145    False
441151    False
441154    False
441158    False
441159    False
441160    False
441161    False
441163    False
441165    False
441168    False
441173    False
441181    False
441194    False
441196    False
441214    False
441226    False
441236    False
441237    False
441238     True
441240    False
441246    False
441253    False
441267    False
441269    False
441270    False
441274    False
441288    False
441300    False
441308    False
441315    False
441338    False
441356    False
441360    False
441364    Fals

>>>>>>>>>>Does the Abstract field end in a period?


Accession
438987    True
439564    True
439671    True
440376    True
440440    True
440524    True
440529    True
440677    True
440718    True
440790    True
440891    True
440922    True
440930    True
440948    True
440963    True
440973    True
441096    True
441097    True
441098    True
441102    True
441106    True
441109    True
441117    True
441119    True
441124    True
441129    True
441143    True
441144    True
441145    True
441151    True
441154    True
441158    True
441159    True
441160    True
441161    True
441163    True
441165    True
441168    True
441173    True
441181    True
441194    True
441196    True
441214    True
441226    True
441236    True
441237    True
441238    True
441240    True
441246    True
441253    True
441267    True
441269    True
441270    True
441274    True
441288    True
441300    True
441308    True
441315    True
441338    True
441356    True
441360    True
441364    True
441378    True
441380    True
441381    True
441382    True


Title                                                                                                    \
Accession                                                                                                                                                                                                             
438987                                                                                                                        Improving Sustainability of Dairy and Forage Production Systems for the Upper Midwest   
439564                                                                                                Incidence of Bacterial Pathogens in Regulated Foods and Applied Processing Technologies for Their Destruction   
439671                                                                                                    Genomic and Epidemiological Parameters to Inform Interventions Strategies for Enteric Diseases of Poultry   
440376                                                                                                                           Advanced Methods for Predictive Modeling of Bacterial Growth and Survival in Foods   
440440                                                                                                   Integrative Genomic and Biological Approaches to Detect and Manage Emerging Foreign Fungal Plant Pathogens   
440524                                                                                                                      Improved Management, Quality and Utilization of Alfalfa for Dairies in the Western U.S.   
440529                                                                                                                          Detection, Quantification and Characterization Technologies for Foodborne Pathogens   
440677                                                                                                                   Elucidating the Pathobiology and Transmission of Transmissible Spongiform Encephalopathies   
440718                                                                                 Innovative Manure Treatment Technologies and Enhanced Soil Health for Agricultural Systems of the Southeastern Coastal Plain   
440790                                                                                                                                Advancement of Sensing Technologies for Food Safety and Security Applications   
440891                                                                   Soil, Crop, and Manure Biochemistry and Molecular Ecology: Bridging Knowledge Gaps in Microbiome Response to Management and Climate Change   
440922                                                                                          Sustainable Management of Manure Nutrients and Environmental Contaminants from Beef and Swine Production Facilities   
440930                                                                                                                 Holistic Tactics to Advance the Microbiological Safety and Quality of the Red Meat Continuum   
440948       Analysis of Genetic Factors that Increase Foodborne Pathogen Fitness, Virulence, and Antimicrobial Resistance Transfer, to Identify Interventions against Salmonella and Campylobacter in Food Animals   
440963                                                                                                                                      Exploration for Natural Enemies in China for Citrus psyllid in the U.S.   
440973     Improving Pre-harvest Produce Safety through Reduction of Pathogen Levels in Agricultural Environments and Development and Validation of Farm-Scale Microbial Quality Model for Irrigation Water Sources   
441096                                                          Developing Agronomically and Environmentally Beneficial Management Practices to Increase the Sustainability and Safety of Animal Manure Utilization   
441097                 

## DATA CHECK: All titles, abstracts MUST end with a period and a space.
### DO all titles and absracts end with a period and space?? (see analyses above checking for period (not space).
### CAUTION: If you rerun on the same kernel, it will add more and more periods. Restart kernel and rerun all code to rerun the block below. The code adds a period and a space to Titles, and just a space to Abstracts (based on analysis of FY22Q3 ARIS data, reviewed 1/22/2023). Your results may differ - comment out as appropriate!

In [10]:
# IF you see the need to add periods, spaces on Titles or abstracts - run the following code to add them.
# Otherwise, do not run this, or comment it out. 

result['Title'] =  result['Title'].astype(str)+'. ' # adding s period, and aspace
result['Abstract'] =  result['Abstract'].astype(str)+' ' # adding a space

result.replace({'. ':'.. .'})

Title                                                                                                     \
Accession                                                                                                                                                                                                               
438987                                                                                                                        Improving Sustainability of Dairy and Forage Production Systems for the Upper Midwest.    
439564                                                                                                Incidence of Bacterial Pathogens in Regulated Foods and Applied Processing Technologies for Their Destruction.    
439671                                                                                                    Genomic and Epidemiological Parameters to Inform Interventions Strategies for Enteric Diseases of Poultry.    
440376                                                                                                                           Advanced Methods for Predictive Modeling of Bacterial Growth and Survival in Foods.    
440440                                                                                                   Integrative Genomic and Biological Approaches to Detect and Manage Emerging Foreign Fungal Plant Pathogens.    
440524                                                                                                                      Improved Management, Quality and Utilization of Alfalfa for Dairies in the Western U.S..    
440529                                                                                                                          Detection, Quantification and Characterization Technologies for Foodborne Pathogens.    
440677                                                                                                                   Elucidating the Pathobiology and Transmission of Transmissible Spongiform Encephalopathies.    
440718                                                                                 Innovative Manure Treatment Technologies and Enhanced Soil Health for Agricultural Systems of the Southeastern Coastal Plain.    
440790                                                                                                                                Advancement of Sensing Technologies for Food Safety and Security Applications.    
440891                                                                   Soil, Crop, and Manure Biochemistry and Molecular Ecology: Bridging Knowledge Gaps in Microbiome Response to Management and Climate Change.    
440922                                                                                          Sustainable Management of Manure Nutrients and Environmental Contaminants from Beef and Swine Production Facilities.    
440930                                                                                                                 Holistic Tactics to Advance the Microbiological Safety and Quality of the Red Meat Continuum.    
440948       Analysis of Genetic Factors that Increase Foodborne Pathogen Fitness, Virulence, and Antimicrobial Resistance Transfer, to Identify Interventions against Salmonella and Campylobacter in Food Animals.    
440963                                                                                                                                      Exploration for Natural Enemies in China for Citrus psyllid in the U.S..    
440973     Improving Pre-harvest Produce Safety through Reduction of Pathogen Levels in Agricultural Environments and Development and Validation of Farm-Scale Microbial Quality Model for Irrigation Water Sources.    
441096                                                          Developing Agronomically and Environmentally Beneficial Management Practices to Increase the Sustainability and Safety of Animal Manure Uti

In [11]:
print('DATA CHECK: All titles, abstracts end with a period and a space.')
print('All titles and absracts end with a period and space??')
print('CAUTION: If you rerun on the same kernel, it will add more and more periods. Restart kernel to rerun!')

# Remove data check columns
result = result.drop('abstract_pd_space', axis = 1)
result = result.drop('title_pd_space', axis = 1)
display(result)

DATA CHECK: All titles, abstracts end with a period and a space.
All titles and absracts end with a period and space??
CAUTION: If you rerun on the same kernel, it will add more and more periods. Restart kernel to rerun!


Title                                                                                                     \
Accession                                                                                                                                                                                                               
438987                                                                                                                        Improving Sustainability of Dairy and Forage Production Systems for the Upper Midwest.    
439564                                                                                                Incidence of Bacterial Pathogens in Regulated Foods and Applied Processing Technologies for Their Destruction.    
439671                                                                                                    Genomic and Epidemiological Parameters to Inform Interventions Strategies for Enteric Diseases of Poultry.    
440376                                                                                                                           Advanced Methods for Predictive Modeling of Bacterial Growth and Survival in Foods.    
440440                                                                                                   Integrative Genomic and Biological Approaches to Detect and Manage Emerging Foreign Fungal Plant Pathogens.    
440524                                                                                                                      Improved Management, Quality and Utilization of Alfalfa for Dairies in the Western U.S..    
440529                                                                                                                          Detection, Quantification and Characterization Technologies for Foodborne Pathogens.    
440677                                                                                                                   Elucidating the Pathobiology and Transmission of Transmissible Spongiform Encephalopathies.    
440718                                                                                 Innovative Manure Treatment Technologies and Enhanced Soil Health for Agricultural Systems of the Southeastern Coastal Plain.    
440790                                                                                                                                Advancement of Sensing Technologies for Food Safety and Security Applications.    
440891                                                                   Soil, Crop, and Manure Biochemistry and Molecular Ecology: Bridging Knowledge Gaps in Microbiome Response to Management and Climate Change.    
440922                                                                                          Sustainable Management of Manure Nutrients and Environmental Contaminants from Beef and Swine Production Facilities.    
440930                                                                                                                 Holistic Tactics to Advance the Microbiological Safety and Quality of the Red Meat Continuum.    
440948       Analysis of Genetic Factors that Increase Foodborne Pathogen Fitness, Virulence, and Antimicrobial Resistance Transfer, to Identify Interventions against Salmonella and Campylobacter in Food Animals.    
440963                                                                                                                                      Exploration for Natural Enemies in China for Citrus psyllid in the U.S..    
440973     Improving Pre-harvest Produce Safety through Reduction of Pathogen Levels in Agricultural Environments and Development and Validation of Farm-Scale Microbial Quality Model for Irrigation Water Sources.    
441096                                                          Developing Agronomically and Environmentally Beneficial Management Practices to Increase the Sustainability and Safety of Animal Manure Uti

In [12]:
# MAKE cogx files.
import xml.etree.cElementTree as ET

try:
    os.mkdir(os.path.sep.join([workingcvs_dir, 'ARIScogx']))
except FileExistsError:
    pass

for t in result.itertuples():
    root = ET.Element("cogito")
    doc = ET.SubElement(root, "doc")
    doc.set('id', str(t.Index))
    
    ET.SubElement(ET.SubElement(doc, "content", zone="articleTitle"), "text", mimetype="text/plain").text = t.Title
    ET.SubElement(ET.SubElement(doc, "content", zone="Abstract"), "text", mimetype="text/plain").text = t.Abstract
    metadata = ET.SubElement(doc, "metadata")
    ET.SubElement(metadata, "a", name="language", value="English")
    metadata = ET.SubElement(doc, "metadata", zone="articleTitle")
    ET.SubElement(metadata, "a", name="language", value="English")
    metadata = ET.SubElement(doc, "metadata", zone="Abstract")
    ET.SubElement(metadata, "a", name="language", value="English")
    
    tree = ET.ElementTree(root)
    tree.write(os.path.sep.join([workingcvs_dir, 'ARIScogx',str(t.Index) + ".cogx"]))
print('Creation of cogx files completed.')
print('Cogx output files to zip for Cogito upload are saved to', os.path.sep.join([workingcvs_dir, 'ARIScogx']))

Creation of cogx files completed.
Cogx output files to zip for Cogito upload are saved to C:\Users\jennifer.woodward\ARISdata\ARISdata_2023_Jan_23\ARIScogx


In [13]:
# to do: add zipping process to code so user does not need to do it.